# The Battle of Neighborhoods - Capstone

In [68]:
#installing libraries
!pip install BeautifulSoup4
!pip install requests
!pip install geopy

In [69]:
#import libraries
import pandas as pd
from bs4 import BeautifulSoup
import requests
import numpy as np
from geopy.geocoders import Nominatim 
from pandas.io.json import json_normalize
import folium
from sklearn.cluster import KMeans
import matplotlib.cm as cm
import matplotlib.colors as colors

pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

## Scraping Data

In [70]:
#scraping html
scrape = requests.get("https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M")
bs = BeautifulSoup(scrape.text, 'lxml')

In [71]:
table = bs.find("table")
table_rows = table.tbody.find_all("tr")

#iterating through the table on wikipedia to scrape the HTML data
data = []
for tr in table_rows:
    td = tr.find_all("td")
    row = [tr.text for tr in td]
    
    # Only process the cells that have an assigned borough. Ignore cells with a borough that is Not assigned.
    if row != [] and row[1] != "Not assigned\n":
        # If a cell has a borough but a "Not assigned" neighborhood, then the neighborhood will be the same as the borough.
        if "Not assigned\n" in row[2]: 
            row[2] = row[1]
        data.append(row)

# Dataframe with 3 columns
df_postalcodes = pd.DataFrame(data, columns = ["Postal Code", "Borough", "Neighborhood"])
df_postalcodes.head()


Postal Code             Borough  \
0       M3A\n        North York\n   
1       M4A\n        North York\n   
2       M5A\n  Downtown Toronto\n   
3       M6A\n        North York\n   
4       M7A\n  Downtown Toronto\n   

                                    Neighborhood  
0                                    Parkwoods\n  
1                             Victoria Village\n  
2                    Regent Park, Harbourfront\n  
3             Lawrence Manor, Lawrence Heights\n  
4  Queen's Park, Ontario Provincial Government\n

In [72]:
df_postalcodes["Postal Code"] = df_postalcodes["Postal Code"].str.replace("\n","")
df_postalcodes["Borough"] = df_postalcodes["Borough"].str.replace("\n","")
df_postalcodes["Neighborhood"] = df_postalcodes["Neighborhood"].str.replace("\n","")
df_postalcodes.head()

Postal Code           Borough                                 Neighborhood
0         M3A        North York                                    Parkwoods
1         M4A        North York                             Victoria Village
2         M5A  Downtown Toronto                    Regent Park, Harbourfront
3         M6A        North York             Lawrence Manor, Lawrence Heights
4         M7A  Downtown Toronto  Queen's Park, Ontario Provincial Government

In [73]:
df_postalcodes = df_postalcodes.groupby(["Postal Code", "Borough"])["Neighborhood"].apply(", ".join).reset_index()
df_postalcodes.head()

Postal Code      Borough                            Neighborhood
0         M1B  Scarborough                          Malvern, Rouge
1         M1C  Scarborough  Rouge Hill, Port Union, Highland Creek
2         M1E  Scarborough       Guildwood, Morningside, West Hill
3         M1G  Scarborough                                  Woburn
4         M1H  Scarborough                               Cedarbrae

In [74]:
df_postalcodes.shape

(103, 3)

In [75]:
df_geocoords = pd.read_csv("Geospatial_Coordinates.csv")
df_geocoords.head()

Postal Code   Latitude  Longitude
0         M1B  43.806686 -79.194353
1         M1C  43.784535 -79.160497
2         M1E  43.763573 -79.188711
3         M1G  43.770992 -79.216917
4         M1H  43.773136 -79.239476

In [76]:
df_toronto = pd.merge(df_postalcodes, df_geocoords, how='left', left_on = 'Postal Code', right_on = 'Postal Code')
df_toronto.head()

Postal Code      Borough                            Neighborhood   Latitude  \
0         M1B  Scarborough                          Malvern, Rouge  43.806686   
1         M1C  Scarborough  Rouge Hill, Port Union, Highland Creek  43.784535   
2         M1E  Scarborough       Guildwood, Morningside, West Hill  43.763573   
3         M1G  Scarborough                                  Woburn  43.770992   
4         M1H  Scarborough                               Cedarbrae  43.773136   

   Longitude  
0 -79.194353  
1 -79.160497  
2 -79.188711  
3 -79.216917  
4 -79.239476

In [77]:
address = "Toronto, Ontario"
geolocator = Nominatim(user_agent="custom")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('Toronto is located at geographical coordinates: {}, {}.'.format(latitude, longitude))

Toronto is located at geographical coordinates: 43.6534817, -79.3839347.


In [78]:
map_toronto = folium.Map(location=[latitude, longitude], zoom_start=13)
map_toronto

In [79]:
for lat, lng, borough, neighborhood in zip(df_toronto['Latitude'], df_toronto['Longitude'], df_toronto['Borough'], df_toronto['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=3,
        popup=label,
        color='green',
        fill=True,
        fill_color='#90EE90',
        fill_opacity=0.6,
        parse_html=False).add_to(map_toronto)  

map_toronto

In [80]:
toronto_data = df_toronto[df_toronto['Borough'].str.contains("Downtown Toronto")].reset_index(drop=True)
print(toronto_data.shape)
toronto_data

(19, 5)


Postal Code           Borough  \
0          M4W  Downtown Toronto   
1          M4X  Downtown Toronto   
2          M4Y  Downtown Toronto   
3          M5A  Downtown Toronto   
4          M5B  Downtown Toronto   
5          M5C  Downtown Toronto   
6          M5E  Downtown Toronto   
7          M5G  Downtown Toronto   
8          M5H  Downtown Toronto   
9          M5J  Downtown Toronto   
10         M5K  Downtown Toronto   
11         M5L  Downtown Toronto   
12         M5S  Downtown Toronto   
13         M5T  Downtown Toronto   
14         M5V  Downtown Toronto   
15         M5W  Downtown Toronto   
16         M5X  Downtown Toronto   
17         M6G  Downtown Toronto   
18         M7A  Downtown Toronto   

                                         Neighborhood   Latitude  Longitude  
0                                            Rosedale  43.679563 -79.377529  
1                         St. James Town, Cabbagetown  43.667967 -79.367675  
2                                Church and Wellesley  43.665860 -79.383160  
3                           Regent Park, Harbourfront  43.654260 -79.360636  
4                            Garden District, Ryerson  43.657162 -79.378937  
5                                      St. James Town  43.651494 -79.375418  
6                                         Berczy Park  43.644771 -79.373306  
7                                  Central Bay Street  43.657952 -79.387383  
8                            Richmond, Adelaide, King  43.650571 -79.384568  
9   Harbourfront East, Union Station, Toronto Islands  43.640816 -79.381752  
10           Toronto Dominion Centre, Design Exchange  43.647177 -79.381576  
11                     Commerce Court, Victoria Hotel  43.648198 -79.379817  
12                     University of Toronto, Harbord  43.662696 -79.400049  
13          Kensington Market, Chinatown, Grange Park  43.653206 -79.400049  
14  CN Tower, King and Spadina, Railway Lands, Har...  43.628947 -79.394420  
15                                     Stn A PO Boxes  43.646435 -79.374846  
16             First Canadian Place, Underground city  43.648429 -79.382280  
17                                           Christie  43.669542 -79.422564  
18        Queen's Park, Ontario Provincial Government  43.662301 -79.389494

In [81]:
map_toronto = folium.Map(location=[latitude, longitude], zoom_start=13)

for lat, lng, label in zip(toronto_data['Latitude'], toronto_data['Longitude'], toronto_data['Neighborhood']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng], 
        radius=5, 
        popup=label, 
        color='green', 
        fill=True, 
        fill_color='#90EE90', 
        fill_opacity=0.6,parse_html=False).add_to(map_toronto)  

map_toronto

In [82]:
# Foursquare API
CLIENT_ID = 'PN25EJIEXEQOSRGHBSLEHDDSJ3M1SSMZNQN3PLJD33WKKYAP' # Put Your Client Id
CLIENT_SECRET = 'LX1XLFWF3GBIW1SVWNZH5WHWXWFW5HQ1I4CAGAILHFDATXR2' # Put You Client Secret 
VERSION = '20200701'
LIMIT = 30

In [83]:

def getNearbyVenues(names, latitudes, longitudes, radius=600):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
        
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, CLIENT_SECRET, VERSION, lat, lng, radius, LIMIT)
        
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        venues_list.append([( name, lat, lng, v['venue']['name'], v['venue']['location']['lat'], v['venue']['location']['lng'], v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 'Neighborhood Latitude', 'Neighborhood Longitude', 'Venue', 'Venue Latitude', 'Venue Longitude', 'Venue Category']
    
    return(nearby_venues)

In [84]:
df = toronto_data
toronto_venues = getNearbyVenues(names=df['Neighborhood'], latitudes=df['Latitude'],longitudes=df['Longitude'])

Rosedale
St. James Town, Cabbagetown
Church and Wellesley
Regent Park, Harbourfront
Garden District, Ryerson
St. James Town
Berczy Park
Central Bay Street
Richmond, Adelaide, King
Harbourfront East, Union Station, Toronto Islands
Toronto Dominion Centre, Design Exchange
Commerce Court, Victoria Hotel
University of Toronto, Harbord
Kensington Market, Chinatown, Grange Park
CN Tower, King and Spadina, Railway Lands, Harbourfront West, Bathurst Quay, South Niagara, Island airport
Stn A PO Boxes
First Canadian Place, Underground city
Christie
Queen's Park, Ontario Provincial Government


In [85]:
print(toronto_venues.shape)
toronto_venues

(519, 7)


Neighborhood  Neighborhood Latitude  \
0                                             Rosedale              43.679563   
1                                             Rosedale              43.679563   
2                                             Rosedale              43.679563   
3                                             Rosedale              43.679563   
4                                             Rosedale              43.679563   
5                          St. James Town, Cabbagetown              43.667967   
6                          St. James Town, Cabbagetown              43.667967   
7                          St. James Town, Cabbagetown              43.667967   
8                          St. James Town, Cabbagetown              43.667967   
9                          St. James Town, Cabbagetown              43.667967   
10                         St. James Town, Cabbagetown              43.667967   
11                         St. James Town, Cabbagetown              43.667967   
12                         St. James Town, Cabbagetown              43.667967   
13                         St. James Town, Cabbagetown              43.667967   
14                         St. James Town, Cabbagetown              43.667967   
15                         St. James Town, Cabbagetown              43.667967   
16                         St. James Town, Cabbagetown              43.667967   
17                         St. James Town, Cabbagetown              43.667967   
18                         St. James Town, Cabbagetown              43.667967   
19                         St. James Town, Cabbagetown              43.667967   
20                         St. James Town, Cabbagetown              43.667967   
21                         St. James Town, Cabbagetown              43.667967   
22                         St. James Town, Cabbagetown              43.667967   
23                         St. James Town, Cabbagetown              43.667967   
24                         St. James Town, Cabbagetown              43.667967   
25                         St. James Town, Cabbagetown              43.667967   
26                         St. James Town, Cabbagetown              43.667967   
27                         St. James Town, Cabbagetown              43.667967   
28                         St. James Town, Cabbagetown              43.667967   
29                         St. James Town, Cabbagetown              43.667967   
30                         St. James Town, Cabbagetown              43.667967   
31                         St. James Town, Cabbagetown              43.667967   
32                         St. James Town, Cabbagetown              43.667967   
33                         St. James Town, Cabbagetown              43.667967   
34                         St. James Town, Cabbagetown              43.667967   
35                                Church and Wellesley              43.665860   
36                                Church and Wellesley              43.665860   
37                                Church and Wellesley              43.665860   
38                                Church and Wellesley              43.665860   
39                                Church and Wellesley              43.665860   
40                                Church and Wellesley              43.665860   
41                                Church and Wellesley              43.665860   
42                                Church and Wellesley              43.665860   
43                                Church and Wellesley              43.665860   
44                                Church and Wellesley              43.665860   
45                                Church and Wellesley              43.665860   
46                                Church and Wellesley              43.665860   
47                                Church and Wellesley              43.665860   
48                                Church and Wellesley              43.66

In [86]:
toronto_venues.groupby('Neighborhood').count()

Neighborhood Latitude  \
Neighborhood                                                                
Berczy Park                                                            30   
CN Tower, King and Spadina, Railway Lands, Harb...                     17   
Central Bay Street                                                     30   
Christie                                                               17   
Church and Wellesley                                                   30   
Commerce Court, Victoria Hotel                                         30   
First Canadian Place, Underground city                                 30   
Garden District, Ryerson                                               30   
Harbourfront East, Union Station, Toronto Islands                      30   
Kensington Market, Chinatown, Grange Park                              30   
Queen's Park, Ontario Provincial Government                            30   
Regent Park, Harbourfront                                              30   
Richmond, Adelaide, King                                               30   
Rosedale                                                                5   
St. James Town                                                         30   
St. James Town, Cabbagetown                                            30   
Stn A PO Boxes                                                         30   
Toronto Dominion Centre, Design Exchange                               30   
University of Toronto, Harbord                                         30   

                                                    Neighborhood Longitude  \
Neighborhood                                                                 
Berczy Park                                                             30   
CN Tower, King and Spadina, Railway Lands, Harb...                      17   
Central Bay Street                                                      30   
Christie                                                                17   
Church and Wellesley                                                    30   
Commerce Court, Victoria Hotel                                          30   
First Canadian Place, Underground city                                  30   
Garden District, Ryerson                                                30   
Harbourfront East, Union Station, Toronto Islands                       30   
Kensington Market, Chinatown, Grange Park                               30   
Queen's Park, Ontario Provincial Government                             30   
Regent Park, Harbourfront                                               30   
Richmond, Adelaide, King                                                30   
Rosedale                                                                 5   
St. James Town                                                          30   
St. James Town, Cabbagetown                                             30   
Stn A PO Boxes                                                          30   
Toronto Dominion Centre, Design Exchange                                30   
University of Toronto, Harbord                                          30   

                                                    Venue  Venue Latitude  \
Neighborhood                                                                
Berczy Park                                            30              30   
CN Tower, King and Spadina, Railway Lands, Harb...     17              17   
Central Bay Street                                     30              30   
Christie                                               17              17   
Church and Wellesley                                   30              30   
Commerce Court, Victoria Hotel                         30              30   
First Canadian Place, Underground city                 30              30   
Garden District, Ryerson                               30              30   
Harbourfront East, Union 

In [87]:
print('{} uniques categories'.format(len(toronto_venues['Venue Category'].unique())))

143 uniques categories


In [88]:
toronto_onehot = pd.get_dummies(toronto_venues[['Venue Category']], prefix="", prefix_sep="")

toronto_onehot['Neighborhood'] = toronto_venues['Neighborhood'] 

fixed_columns = [toronto_onehot.columns[-1]] + list(toronto_onehot.columns[:-1])
toronto_onehot = toronto_onehot[fixed_columns]

toronto_onehot

Yoga Studio  Airport  Airport Food Court  Airport Lounge  \
0              0        0                   0               0   
1              0        0                   0               0   
2              0        0                   0               0   
3              0        0                   0               0   
4              0        0                   0               0   
5              0        0                   0               0   
6              0        0                   0               0   
7              0        0                   0               0   
8              0        0                   0               0   
9              0        0                   0               0   
10             0        0                   0               0   
11             0        0                   0               0   
12             0        0                   0               0   
13             0        0                   0               0   
14             0        0                   0               0   
15             0        0                   0               0   
16             0        0                   0               0   
17             0        0                   0               0   
18             0        0                   0               0   
19             0        0                   0               0   
20             0        0                   0               0   
21             0        0                   0               0   
22             0        0                   0               0   
23             0        0                   0               0   
24             0        0                   0               0   
25             0        0                   0               0   
26             0        0                   0               0   
27             0        0                   0               0   
28             0        0                   0               0   
29             0        0                   0               0   
30             0        0                   0               0   
31             0        0                   0               0   
32             0        0                   0               0   
33             0        0                   0               0   
34             0        0                   0               0   
35             0        0                   0               0   
36             0        0                   0               0   
37             0        0                   0               0   
38             0        0                   0               0   
39             0        0                   0               0   
40             0        0                   0               0   
41             0        0                   0               0   
42             0        0                   0               0   
43             0        0                   0               0   
44             0        0                   0               0   
45             0        0                   0               0   
46             0        0                   0               0   
47             0        0                   0               0   
48             0        0                   0               0   
49             0        0                   0               0   
50             0        0                   0               0   
51             0        0                   0               0   
52             0        0                   0               0   
53             0        0                   0               0   
54             0        0                   0               0   
55             0        0                   0               0   
56             0        0                   0               0   
57             0        0                   0               0   
58             0        0                   0               0   
59             0        0                   0               0   
60             0        0               

In [89]:
toronto_onehot.shape

(519, 143)

In [90]:
toronto_grouped = toronto_onehot.groupby('Neighborhood').mean().reset_index()
toronto_grouped

Neighborhood  Yoga Studio   Airport  \
0                                         Berczy Park     0.000000  0.000000   
1   CN Tower, King and Spadina, Railway Lands, Har...     0.000000  0.058824   
2                                  Central Bay Street     0.033333  0.000000   
3                                            Christie     0.000000  0.000000   
4                                Church and Wellesley     0.000000  0.000000   
5                      Commerce Court, Victoria Hotel     0.000000  0.000000   
6              First Canadian Place, Underground city     0.000000  0.000000   
7                            Garden District, Ryerson     0.000000  0.000000   
8   Harbourfront East, Union Station, Toronto Islands     0.000000  0.000000   
9           Kensington Market, Chinatown, Grange Park     0.000000  0.000000   
10        Queen's Park, Ontario Provincial Government     0.033333  0.000000   
11                          Regent Park, Harbourfront     0.000000  0.000000   
12                           Richmond, Adelaide, King     0.000000  0.000000   
13                                           Rosedale     0.000000  0.000000   
14                                     St. James Town     0.000000  0.000000   
15                        St. James Town, Cabbagetown     0.000000  0.000000   
16                                     Stn A PO Boxes     0.000000  0.000000   
17           Toronto Dominion Centre, Design Exchange     0.000000  0.000000   
18                     University of Toronto, Harbord     0.033333  0.000000   

    Airport Food Court  Airport Lounge  Airport Service  Airport Terminal  \
0             0.000000        0.000000         0.000000          0.000000   
1             0.058824        0.117647         0.117647          0.117647   
2             0.000000        0.000000         0.000000          0.000000   
3             0.000000        0.000000         0.000000          0.000000   
4             0.000000        0.000000         0.000000          0.000000   
5             0.000000        0.000000         0.000000          0.000000   
6             0.000000        0.000000         0.000000          0.000000   
7             0.000000        0.000000         0.000000          0.000000   
8             0.000000        0.000000         0.000000          0.000000   
9             0.000000        0.000000         0.000000          0.000000   
10            0.000000        0.000000         0.000000          0.000000   
11            0.000000        0.000000         0.000000          0.000000   
12            0.000000        0.000000         0.000000          0.000000   
13            0.000000        0.000000         0.000000          0.000000   
14            0.000000        0.000000         0.000000          0.000000   
15            0.000000        0.000000         0.000000          0.000000   
16            0.000000        0.000000         0.000000          0.000000   
17            0.000000        0.000000         0.000000          0.000000   
18            0.000000        0.000000         0.000000          0.000000   

    American Restaurant  Aquarium  Art Gallery  Art Museum  \
0              0.000000  0.000000     0.033333    0.000000   
1              0.000000  0.000000     0.000000    0.000000   
2              0.000000  0.000000     0.000000    0.033333   
3              0.000000  0.000000     0.000000    0.000000   
4              0.000000  0.000000     0.000000    0.000000   
5              0.066667  0.000000     0.033333    0.000000   
6              0.033333  0.000000     0.033333    0.000000   
7              0.000000  0.000000     0.000000    0.000000   
8              0.000000  0.033333     0.033333    0.000000   
9              0.000000  0.000000     0.000000    0.000000   
10             0.000000  0.000000     0.000000    0.000000   
11             0.000000  0.000000     0.000000    0.000000   
12             0.033333  0.000000     0.000000    0.000000   
13             0.000000  0.0000

In [91]:
toronto_grouped.shape

(19, 143)

In [92]:
num_top_venues = 5
for n in toronto_grouped['Neighborhood']:
    print("----"+n+"----")
    temp = toronto_grouped[toronto_grouped['Neighborhood'] == n].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Berczy Park----
                 venue  freq
0  Japanese Restaurant  0.07
1   Seafood Restaurant  0.07
2       Farmers Market  0.07
3         Cocktail Bar  0.07
4          Coffee Shop  0.07


----CN Tower, King and Spadina, Railway Lands, Harbourfront West, Bathurst Quay, South Niagara, Island airport----
              venue  freq
0       Coffee Shop  0.12
1    Airport Lounge  0.12
2   Airport Service  0.12
3  Airport Terminal  0.12
4             Plane  0.06


----Central Bay Street----
                venue  freq
0         Coffee Shop  0.17
1  Italian Restaurant  0.07
2                Café  0.07
3         Pizza Place  0.03
4     Bubble Tea Shop  0.03


----Christie----
           venue  freq
0  Grocery Store  0.24
1           Café  0.18
2           Park  0.12
3    Coffee Shop  0.06
4      Nightclub  0.06


----Church and Wellesley----
             venue  freq
0          Gay Bar  0.07
1      Coffee Shop  0.07
2              Gym  0.03
3     Dance Studio  0.03
4  Bubble Tea Shop  0.0

In [93]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    return row_categories_sorted.index.values[0:num_top_venues]

print(return_most_common_venues(toronto_grouped.iloc[ind, :], num_top_venues=5))

['Bakery' 'Restaurant' 'Japanese Restaurant' 'Bookstore' 'Café']


In [94]:
num_top_venues = 10
indicators = ['st', 'nd', 'rd']

columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = toronto_grouped['Neighborhood']

for ind in np.arange(toronto_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(toronto_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.shape

(19, 11)

In [95]:
km = KMeans(n_clusters=3, init='k-means++', max_iter=100, n_init=1, 
  verbose=True)

In [96]:
kclusters = 10
toronto_grouped_clustering = toronto_grouped.drop('Neighborhood', 1)

kmeans = KMeans(n_clusters=kclusters, random_state=1).fit(toronto_grouped_clustering)

print(kmeans.labels_[0:10])
print(len(kmeans.labels_))

[7 6 5 2 8 1 1 1 9 4]
19


In [97]:
df

Postal Code           Borough  \
0          M4W  Downtown Toronto   
1          M4X  Downtown Toronto   
2          M4Y  Downtown Toronto   
3          M5A  Downtown Toronto   
4          M5B  Downtown Toronto   
5          M5C  Downtown Toronto   
6          M5E  Downtown Toronto   
7          M5G  Downtown Toronto   
8          M5H  Downtown Toronto   
9          M5J  Downtown Toronto   
10         M5K  Downtown Toronto   
11         M5L  Downtown Toronto   
12         M5S  Downtown Toronto   
13         M5T  Downtown Toronto   
14         M5V  Downtown Toronto   
15         M5W  Downtown Toronto   
16         M5X  Downtown Toronto   
17         M6G  Downtown Toronto   
18         M7A  Downtown Toronto   

                                         Neighborhood   Latitude  Longitude  
0                                            Rosedale  43.679563 -79.377529  
1                         St. James Town, Cabbagetown  43.667967 -79.367675  
2                                Church and Wellesley  43.665860 -79.383160  
3                           Regent Park, Harbourfront  43.654260 -79.360636  
4                            Garden District, Ryerson  43.657162 -79.378937  
5                                      St. James Town  43.651494 -79.375418  
6                                         Berczy Park  43.644771 -79.373306  
7                                  Central Bay Street  43.657952 -79.387383  
8                            Richmond, Adelaide, King  43.650571 -79.384568  
9   Harbourfront East, Union Station, Toronto Islands  43.640816 -79.381752  
10           Toronto Dominion Centre, Design Exchange  43.647177 -79.381576  
11                     Commerce Court, Victoria Hotel  43.648198 -79.379817  
12                     University of Toronto, Harbord  43.662696 -79.400049  
13          Kensington Market, Chinatown, Grange Park  43.653206 -79.400049  
14  CN Tower, King and Spadina, Railway Lands, Har...  43.628947 -79.394420  
15                                     Stn A PO Boxes  43.646435 -79.374846  
16             First Canadian Place, Underground city  43.648429 -79.382280  
17                                           Christie  43.669542 -79.422564  
18        Queen's Park, Ontario Provincial Government  43.662301 -79.389494

In [98]:
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)
toronto_merged = df
toronto_merged = toronto_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

toronto_merged

Postal Code           Borough  \
0          M4W  Downtown Toronto   
1          M4X  Downtown Toronto   
2          M4Y  Downtown Toronto   
3          M5A  Downtown Toronto   
4          M5B  Downtown Toronto   
5          M5C  Downtown Toronto   
6          M5E  Downtown Toronto   
7          M5G  Downtown Toronto   
8          M5H  Downtown Toronto   
9          M5J  Downtown Toronto   
10         M5K  Downtown Toronto   
11         M5L  Downtown Toronto   
12         M5S  Downtown Toronto   
13         M5T  Downtown Toronto   
14         M5V  Downtown Toronto   
15         M5W  Downtown Toronto   
16         M5X  Downtown Toronto   
17         M6G  Downtown Toronto   
18         M7A  Downtown Toronto   

                                         Neighborhood   Latitude  Longitude  \
0                                            Rosedale  43.679563 -79.377529   
1                         St. James Town, Cabbagetown  43.667967 -79.367675   
2                                Church and Wellesley  43.665860 -79.383160   
3                           Regent Park, Harbourfront  43.654260 -79.360636   
4                            Garden District, Ryerson  43.657162 -79.378937   
5                                      St. James Town  43.651494 -79.375418   
6                                         Berczy Park  43.644771 -79.373306   
7                                  Central Bay Street  43.657952 -79.387383   
8                            Richmond, Adelaide, King  43.650571 -79.384568   
9   Harbourfront East, Union Station, Toronto Islands  43.640816 -79.381752   
10           Toronto Dominion Centre, Design Exchange  43.647177 -79.381576   
11                     Commerce Court, Victoria Hotel  43.648198 -79.379817   
12                     University of Toronto, Harbord  43.662696 -79.400049   
13          Kensington Market, Chinatown, Grange Park  43.653206 -79.400049   
14  CN Tower, King and Spadina, Railway Lands, Har...  43.628947 -79.394420   
15                                     Stn A PO Boxes  43.646435 -79.374846   
16             First Canadian Place, Underground city  43.648429 -79.382280   
17                                           Christie  43.669542 -79.422564   
18        Queen's Park, Ontario Provincial Government  43.662301 -79.389494   

    Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
0                3                  Park            Playground   
1                4                  Park    Italian Restaurant   
2                8               Gay Bar           Coffee Shop   
3                0           Coffee Shop                Bakery   
4                1                  Café           Coffee Shop   
5                7             Gastropub                  Café   
6                7          Cocktail Bar   Japanese Restaurant   
7                5           Coffee Shop    Italian Restaurant   
8                1                  Café           Coffee Shop   
9                9                  Park                 Plaza   
10               1           Coffee Shop                  Café   
11               1                  Café           Coffee Shop   
12               4                Bakery            Restaurant   
13               4                  Café                Bakery   
14               6           Coffee Shop        Airport Lounge   
15               7    Seafood Restaurant        Farmers Market   
16               1                  Café           Coffee Shop   
17               2         Grocery Store                  Café   
18               5           Coffee Shop                  Park   

   3rd Most Common Venue  4th Most Common Venue  5th Most Common Venue  \
0                  Trail               Wine Bar           Concert Hall   
1              Gastropub                   Café             Restaurant   
2                   Park           Burger Joint              Juice Bar   
3                   Park         Breakfast Spot  Performing Arts Venue   
4         

In [99]:
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

x = np.arange(kclusters)
ys = [i+x+(i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

markers_colors = []
for lat, lon, poi, cluster in zip(toronto_merged['Latitude'], toronto_merged['Longitude'], toronto_merged['Neighborhood'],kmeans.labels_):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker([lat, lon], radius=5, popup=label, color=rainbow[cluster-1], fill=True, fill_color=rainbow[cluster-1], fill_opacity=0.7).add_to(map_clusters)

map_clusters

In [100]:
print("All done!")

All done!
